# Train n-gram language model with KenLM on Colab

See https://colab.research.google.com/github/patrickvonplaten/notebooks/blob/master/Boosting_Wav2Vec2_with_n_grams_in_Transformers.ipynb#scrollTo=X9qg4FPt2zi8 for detailed explanation on how to use KenLM to boost wav2vec2 fine-tuned models on 🤗

Install KenLM

In [4]:
!sudo apt install build-essential cmake libboost-system-dev libboost-thread-dev libboost-program-options-dev libboost-test-dev libeigen3-dev zlib1g-dev libbz2-dev liblzma-dev

The operation couldn’t be completed. Unable to locate a Java Runtime that supports apt.
Please visit http://www.java.com for information on installing Java.



In [ ]:
!wget -O - https://kheafield.com/code/kenlm.tar.gz | tar xz

In [3]:
!mkdir kenlm/build && cd kenlm/build && cmake .. && make -j2
!ls kenlm/build/bin

-- The C compiler identification is GNU 7.5.0
-- The CXX compiler identification is GNU 7.5.0
-- Check for working C compiler: /usr/bin/cc
-- Check for working C compiler: /usr/bin/cc -- works
-- Detecting C compiler ABI info
-- Detecting C compiler ABI info - done
-- Detecting C compile features
-- Detecting C compile features - done
-- Check for working CXX compiler: /usr/bin/c++
-- Check for working CXX compiler: /usr/bin/c++ -- works
-- Detecting CXX compiler ABI info
-- Detecting CXX compiler ABI info - done
-- Detecting CXX compile features
-- Detecting CXX compile features - done
-- Looking for pthread.h
-- Looking for pthread.h - found
-- Looking for pthread_create
-- Looking for pthread_create - not found
-- Looking for pthread_create in pthreads
-- Looking for pthread_create in pthreads - not found
-- Looking for pthread_create in pthread
-- Looking for pthread_create in pthread - found
-- Found Threads: TRUE  
-- Boost version: 1.65.1
-- Found the following Boost libraries:


Install 🤗 dependencies

In [4]:
!pip install datasets transformers

     |████████████████████████████████| 311 kB 5.3 MB/s 
     |████████████████████████████████| 3.4 MB 39.8 MB/s 
     |████████████████████████████████| 1.1 MB 54.7 MB/s 
     |████████████████████████████████| 243 kB 41.5 MB/s 
     |████████████████████████████████| 67 kB 5.1 MB/s 
     |████████████████████████████████| 133 kB 50.2 MB/s 
     |████████████████████████████████| 596 kB 56.2 MB/s 
     |████████████████████████████████| 3.3 MB 46.1 MB/s 
     |████████████████████████████████| 895 kB 51.6 MB/s 
     |████████████████████████████████| 144 kB 51.5 MB/s 
     |████████████████████████████████| 271 kB 56.7 MB/s 
     |████████████████████████████████| 94 kB 3.0 MB/s 
  Attempting uninstall: pyyaml
    Found existing installation: PyYAML 3.13
    Uninstalling PyYAML-3.13:
      Successfully uninstalled PyYAML-3.13


Load preprocessed dataset from 🤗 and write it to file as required by KenLM

In [5]:
from datasets import load_dataset

# change to your dataset path
username = "hf-test"  
target_lang = "sv"

dataset = load_dataset(f"{username}/{target_lang}_corpora_parliament_processed", split="train")

with open("text.txt", "w") as file:
  file.write(" ".join(dataset["text"]))

Downloading:   0%|          | 0.00/1.16k [00:00<?, ?B/s]

Using custom data configuration hf-test--swedish_corpora_parliament_processed-56ded20e2faa0852


  0%|          | 0/1 [00:00<?, ?it/s]

Downloading:   0%|          | 0.00/159M [00:00<?, ?B/s]

  0%|          | 0/1 [00:00<?, ?it/s]

Dataset parquet downloaded and prepared to /root/.cache/huggingface/datasets/parquet/hf-test--swedish_corpora_parliament_processed-56ded20e2faa0852/0.0.0/1638526fd0e8d960534e2155dc54fdff8dce73851f21f031d2fb9c2cf757c121. Subsequent calls will reuse this data.


Train 5-gram language model

In [6]:
!kenlm/build/bin/lmplz -o 5 <"text.txt" > "5gram.arpa"

=== 1/5 Counting and sorting n-grams ===
Reading /content/text.txt
----5---10---15---20---25---30---35---40---45---50---55---60---65---70---75---80---85---90---95--100
tcmalloc: large alloc 1918697472 bytes == 0x5623caa4e000 @  0x7fe627aa41e7 0x5623c8d517a2 0x5623c8cec51e 0x5623c8ccb2eb 0x5623c8cb7066 0x7fe625c3dbf7 0x5623c8cb8baa
tcmalloc: large alloc 8953896960 bytes == 0x56243d01e000 @  0x7fe627aa41e7 0x5623c8d517a2 0x5623c8d407ca 0x5623c8d41208 0x5623c8ccb308 0x5623c8cb7066 0x7fe625c3dbf7 0x5623c8cb8baa
****************************************************************************************************
Unigram tokens 42153890 types 360209
=== 2/5 Calculating and sorting adjusted counts ===
Chain sizes: 1:4322508 2:1062773568 3:1992700672 4:3188320768 5:4649634816
tcmalloc: large alloc 4649639936 bytes == 0x5623caa4e000 @  0x7fe627aa41e7 0x5623c8d517a2 0x5623c8d407ca 0x5623c8d41208 0x5623c8ccb8d7 0x5623c8cb7066 0x7fe625c3dbf7 0x5623c8cb8baa
tcmalloc: large alloc 1992704000 bytes == 

Check head of file

In [7]:
!head -20 5gram.arpa

\data\
ngram 1=360208
ngram 2=5476741
ngram 3=18177681
ngram 4=30374983
ngram 5=37231651

\1-grams:
-6.770219	<unk>	0
0	<s>	-0.11831701
-4.6095004	återupptagande	-1.2174699
-2.2361007	av	-0.79668784
-4.8163533	sessionen	-0.37327805
-2.2251768	jag	-1.4205662
-4.181505	förklarar	-0.56261665
-3.5790775	europaparlamentets	-0.63611007
-4.771945	session	-0.3647111
-5.8043895	återupptagen	-0.3058712
-2.8580177	efter	-0.7557702
-5.199537	avbrottet	-0.43322718


Add end-of-sentence token "\</s>" 

In [8]:
with open("5gram.arpa", "r") as read_file, open("5gram_sv_lm.arpa", "w") as write_file:
  has_added_eos = False
  for line in read_file:
    if not has_added_eos and "ngram 1=" in line:
      count=line.strip().split("=")[-1]
      write_file.write(line.replace(f"{count}", f"{int(count)+1}"))
    elif not has_added_eos and "<s>" in line:
      write_file.write(line)
      write_file.write(line.replace("<s>", "</s>"))
      has_added_eos = True
    else:
      write_file.write(line)

Check head of file

In [9]:
!head -20 5gram_sv_lm.arpa

\data\
ngram 1=360209
ngram 2=5476741
ngram 3=18177681
ngram 4=30374983
ngram 5=37231651

\1-grams:
-6.770219	<unk>	0
0	<s>	-0.11831701
0	</s>	-0.11831701
-4.6095004	återupptagande	-1.2174699
-2.2361007	av	-0.79668784
-4.8163533	sessionen	-0.37327805
-2.2251768	jag	-1.4205662
-4.181505	förklarar	-0.56261665
-3.5790775	europaparlamentets	-0.63611007
-4.771945	session	-0.3647111
-5.8043895	återupptagen	-0.3058712
-2.8580177	efter	-0.7557702


Compress arpa file by converting it to bin

In [11]:
!kenlm/build/bin/build_binary 5gram_sv_lm.arpa 5gram_sv_lm.bin

Reading 5gram_sv_lm.arpa
----5---10---15---20---25---30---35---40---45---50---55---60---65---70---75---80---85---90---95--100
****************************************************************************************************
SUCCESS


Download file to local machine (use Chrome if it fails on another browser).

In [12]:
from google.colab import files
files.download("5gram_sv_lm.bin") 

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>